<a href="https://colab.research.google.com/github/kahochan919/DSAA5024/blob/main/DSAA5024_GroupProject.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Initialization

In [21]:
!pip install plotly pandas

# Setup the folders
!mkdir save_results

FOLDERNAME = '/content/'
import sys
sys.path.append(FOLDERNAME)

# Import libraries
from enum import Enum
import numpy as np
import pandas as pd
from google.colab import files

import warnings
warnings.filterwarnings("ignore")

import plotly.express as px
import pandas as pd
import json

import kagglehub
from kagglehub import KaggleDatasetAdapter


mkdir: cannot create directory ‘save_results’: File exists


# Download Data

In [22]:
! gdown --id 1475aFy3_SSYb6JMQ1li7Wx8enO3Nq1k2

! mkdir ~/.kaggle/
! mv kaggle.json ~/.kaggle/
! chmod 600 ~/.kaggle/kaggle.json

# Vaccination progress
! kaggle datasets download gpreda/covid-world-vaccination-progress
# Population Over Countries in 2021
! gdown --id 1nJkmgzjPq6Tzwi4EIUc3oTByDYHrGiaV
# Covid Death Cases from WHO
!wget https://srhdpeuwpubsa.blob.core.windows.net/whdh/COVID/WHO-COVID-19-global-daily-data.csv -O /content/who_death.csv
# Countries Coordinates
# !wget https://raw.githubusercontent.com/plotly/datasets/master/gapminder_with_codes.csv -O countriesCoordinates.csv

! unzip covid-world-vaccination-progress.zip
! rm covid-world-vaccination-progress.zip

/usr/local/lib/python3.12/dist-packages/gdown/__main__.py:140: FutureWarning: Option `--id` was deprecated in version 4.3.1 and will be removed in 5.0. You don't need to pass it anymore to use a file ID.
  warnings.warn(
Downloading...
From: https://drive.google.com/uc?id=1475aFy3_SSYb6JMQ1li7Wx8enO3Nq1k2
To: /content/kaggle.json
100% 65.0/65.0 [00:00<00:00, 212kB/s]
mkdir: cannot create directory ‘/root/.kaggle/’: File exists
Dataset URL: https://www.kaggle.com/datasets/gpreda/covid-world-vaccination-progress
License(s): CC0-1.0
  0% 0.00/1.94M [00:00<?, ?B/s]
100% 1.94M/1.94M [00:00<00:00, 586MB/s]
/usr/local/lib/python3.12/dist-packages/gdown/__main__.py:140: FutureWarning: Option `--id` was deprecated in version 4.3.1 and will be removed in 5.0. You don't need to pass it anymore to use a file ID.
  warnings.warn(
Downloading...
From: https://drive.google.com/uc?id=1nJkmgzjPq6Tzwi4EIUc3oTByDYHrGiaV
To: /content/2021_population.csv
100% 17.7k/17.7k [00:00<00:00, 33.6MB/s]
--2025-12-0

In [23]:
# Loading datasets to DataFrame
vaccineDf = pd.read_csv('country_vaccinations.csv')
vaccineManufacturerDf = pd.read_csv('country_vaccinations_by_manufacturer.csv')
populationDf = pd.read_csv('2021_population.csv')
whoDeathDf = pd.read_csv('who_death.csv')

In [24]:
# Check Datasets validity

print('########### Countries Vaccination Records ###########')
print(vaccineDf.head())
print()
print('########### Manufacturer Vaccination Records ###########')
print(vaccineManufacturerDf.head())
print()
print('########### 2021 population ###########')
print(populationDf.head())
print()
print('########### COVID WHO Records ###########')
print(whoDeathDf.head())

########### Countries Vaccination Records ###########
       country iso_code        date  total_vaccinations  people_vaccinated  \
0  Afghanistan      AFG  2021-02-22                 0.0                0.0   
1  Afghanistan      AFG  2021-02-23                 NaN                NaN   
2  Afghanistan      AFG  2021-02-24                 NaN                NaN   
3  Afghanistan      AFG  2021-02-25                 NaN                NaN   
4  Afghanistan      AFG  2021-02-26                 NaN                NaN   

   people_fully_vaccinated  daily_vaccinations_raw  daily_vaccinations  \
0                      NaN                     NaN                 NaN   
1                      NaN                     NaN              1367.0   
2                      NaN                     NaN              1367.0   
3                      NaN                     NaN              1367.0   
4                      NaN                     NaN              1367.0   

   total_vaccinations_per_hundre

# Process Data Frame to valid inputs

## Master Investigation

In [25]:
tempdf = pd.merge(vaccineDf[['country', 'iso_code', 'date', 'total_vaccinations', 'people_vaccinated', 'people_fully_vaccinated', 'daily_vaccinations_raw', 'daily_vaccinations']],
                  populationDf[['iso_code', '2021_last_updated', 'area', 'density_sq_km']], on='iso_code', how='left')
masterdf = pd.merge(tempdf[['country', 'iso_code', 'date', 'total_vaccinations', 'people_vaccinated', 'people_fully_vaccinated', 'daily_vaccinations_raw', 'daily_vaccinations', '2021_last_updated', 'area', 'density_sq_km']],
                  whoDeathDf[['Country', 'New_cases', 'New_deaths', 'Cumulative_cases', 'Cumulative_deaths', 'Date_reported']],
                  left_on=['country', 'date'],
                  right_on=['Country', 'Date_reported'],
                  how='left')[['country', 'iso_code', 'date', 'total_vaccinations', 'people_vaccinated', 'people_fully_vaccinated', 'daily_vaccinations_raw', 'daily_vaccinations', '2021_last_updated', 'area', 'density_sq_km', 'New_cases', 'New_deaths', 'Cumulative_cases', 'Cumulative_deaths', 'Date_reported']]

masterdf['2021_last_updated'] = masterdf['2021_last_updated'].str.replace(',', '', regex=False)
masterdf['2021_last_updated'] = pd.to_numeric(masterdf['2021_last_updated'], errors='coerce').astype('Float64')

masterdf['area'] = masterdf['area'].str.replace(' sq_km', '', regex=False)
masterdf['area'] = masterdf['area'].str.replace(',', '', regex=False)
masterdf['area'] = pd.to_numeric(masterdf['area'], errors='coerce').astype('Float64')

masterdf['density_sq_km'] = masterdf['density_sq_km'].str.replace('/sq_km', '', regex=False)
masterdf['density_sq_km'] = masterdf['density_sq_km'].str.replace(',', '', regex=False)
masterdf['density_sq_km'] = pd.to_numeric(masterdf['density_sq_km'], errors='coerce').astype('Float64')


masterdf['date'] = pd.to_datetime(masterdf['date'], format='%Y-%m-%d', errors='coerce')
masterdf = masterdf.rename(columns={'2021_last_updated': '2021_population', 'density_sq_km': 'density'})

In [26]:
# Check no populations
# empty_rows = masterdf[masterdf['2021_population'].isnull()]
# countries_list = empty_rows['country'].tolist()

# unique_countries = list(set(countries_list))
# print(unique_countries)

# pop_df = vaccineDf[vaccineDf['country'].isin(['British Virgin Islands', 'England', 'Northern Cyprus', 'Jersey', 'Saint Helena', 'Scotland', 'Wales', 'Pitcairn', 'Bonaire Sint Eustatius and Saba', 'Guernsey', 'Northern Ireland', 'Sint Maarten (Dutch part)', 'Eswatini', 'Kosovo'])]

# unique_iso = pop_df['iso_code'].tolist()
# unique_iso = list(set(unique_iso))
# print(unique_iso)



## Vaccine Investigations

In [27]:
manufacturerDf = vaccineManufacturerDf.drop_duplicates(subset=['location', 'vaccine'], keep='last')
deathDf = whoDeathDf.drop_duplicates(subset=['Country'], keep='last')

tempdf = pd.merge(manufacturerDf[['location', 'vaccine', 'total_vaccinations']],
                  deathDf[['Country', 'Cumulative_cases', 'Cumulative_deaths']],
                  left_on='location', right_on='Country', how='inner')
vaccinedf = tempdf[['location', 'vaccine', 'total_vaccinations', 'Cumulative_cases', 'Cumulative_deaths']]

print(vaccinedf.head())

    location             vaccine  total_vaccinations  Cumulative_cases  \
0  Argentina             CanSino              610540          10117518   
1  Argentina             Moderna             6507561          10117518   
2  Argentina  Oxford/AstraZeneca            25977231          10117518   
3  Argentina     Pfizer/BioNTech            14681054          10117518   
4  Argentina   Sinopharm/Beijing            28322602          10117518   

   Cumulative_deaths  
0             130820  
1             130820  
2             130820  
3             130820  
4             130820  


In [28]:
vaccinedf_export = vaccinedf.copy()
vaccinedf_export['id'] = vaccinedf_export.index
print(vaccinedf_export)
vaccinedf_export.to_json('save_results/vaccine.json', orient='records', indent=2)

      location             vaccine  total_vaccinations  Cumulative_cases  \
0    Argentina             CanSino              610540          10117518   
1    Argentina             Moderna             6507561          10117518   
2    Argentina  Oxford/AstraZeneca            25977231          10117518   
3    Argentina     Pfizer/BioNTech            14681054          10117518   
4    Argentina   Sinopharm/Beijing            28322602          10117518   
..         ...                 ...                 ...               ...   
165    Ukraine     Pfizer/BioNTech            14774013           5554185   
166    Ukraine             Sinovac             9802231           5554185   
167    Uruguay  Oxford/AstraZeneca               90732           1043085   
168    Uruguay     Pfizer/BioNTech             2476595           1043085   
169    Uruguay             Sinovac             3247932           1043085   

     Cumulative_deaths   id  
0               130820    0  
1               130820    1

# Data Export for Static web page

## Vaccination, Death over Time

In [29]:
print(masterdf.head())

       country iso_code       date  total_vaccinations  people_vaccinated  \
0  Afghanistan      AFG 2021-02-22                 0.0                0.0   
1  Afghanistan      AFG 2021-02-23                 NaN                NaN   
2  Afghanistan      AFG 2021-02-24                 NaN                NaN   
3  Afghanistan      AFG 2021-02-25                 NaN                NaN   
4  Afghanistan      AFG 2021-02-26                 NaN                NaN   

   people_fully_vaccinated  daily_vaccinations_raw  daily_vaccinations  \
0                      NaN                     NaN                 NaN   
1                      NaN                     NaN              1367.0   
2                      NaN                     NaN              1367.0   
3                      NaN                     NaN              1367.0   
4                      NaN                     NaN              1367.0   

   2021_population      area  density  New_cases  New_deaths  \
0       39939293.0  652230.0

In [30]:
masterdf_export = masterdf[['country', 'iso_code', 'date', 'total_vaccinations', 'daily_vaccinations', 'Cumulative_cases', 'Cumulative_deaths']]
masterdf_export['id'] = masterdf_export.index  # Unique ID for D3 key function
masterdf_export['date'] = masterdf_export.date.dt.strftime('%Y-%m-%dT%H:%M:%S')

# print(masterdf_export)
masterdf_export.to_json('save_results/data.json', orient='records', indent=2)

In [31]:
summarydf = masterdf_export.groupby('date').agg({
    'total_vaccinations': 'sum', 'Cumulative_cases': 'sum', 'Cumulative_deaths': 'sum'}).round(2)
summarydf['id'] = summarydf.index # Unique ID for D3 key function
summarydf['total_vaccinations'] = pd.to_numeric(summarydf['total_vaccinations'], errors='coerce').astype('Int64')
summarydf['Cumulative_cases'] = pd.to_numeric(summarydf['Cumulative_cases'], errors='coerce').astype('Int64')
summarydf['Cumulative_deaths'] = pd.to_numeric(summarydf['Cumulative_deaths'], errors='coerce').astype('Int64')

summarydf = summarydf.reset_index()
# print(summarydf)
summarydf.to_json('save_results/summary.json', orient='records', indent=2)

In [32]:
fig = px.line(masterdf_export, x='date', y='total_vaccinations', color='country',
              title='Cumulative Vaccinations over time',
              hover_data=['total_vaccinations'])
fig.update_layout(height=600, template='plotly_white')

In [33]:
casefig = px.line(masterdf_export, x='date', y='Cumulative_cases', color='country',
              title='Cumulative Cases over time',
              hover_data=['Cumulative_cases'])
casefig.update_layout(height=600, template='plotly_white')

In [34]:
deathfig = px.line(masterdf_export, x='date', y='Cumulative_deaths', color='country',
              title='Cumulative Deaths over time',
              hover_data=['Cumulative_deaths'])
deathfig.update_layout(height=600, template='plotly_white')

In [35]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Multi-line plot
summary_fig = go.Figure()

# Add each metric as separate line
summary_fig.add_trace(go.Scatter(
    x=summarydf['date'], y=summarydf['total_vaccinations'],
    mode='lines+markers', name='Total Vaccinations',
    line=dict(color='green', width=1)
))

summary_fig.add_trace(go.Scatter(
    x=summarydf['date'], y=summarydf['Cumulative_deaths'],
    mode='lines+markers', name='Total Deaths',
    line=dict(color='red', width=1)
))

summary_fig.add_trace(go.Scatter(
    x=summarydf['date'], y=summarydf['Cumulative_cases'],
    mode='lines+markers', name='Total Cases',
    line=dict(color='blue', width=1)
))

summary_fig.update_layout(
    title='Vaccinations over cases and deaths dashboard',
    xaxis_title='Date', yaxis_title='Value',
    height=600, template='plotly_white'
)
summary_fig.show()

In [36]:
map_masterdf = masterdf_export[['country', 'iso_code', 'date', 'total_vaccinations', 'Cumulative_cases', 'Cumulative_deaths']]
map_masterdf = map_masterdf.drop_duplicates(subset=['country'], keep='last')
map_masterdf['total_vaccinations'] = np.log(map_masterdf['total_vaccinations'])
map_masterdf['Cumulative_cases'] = np.log(map_masterdf['Cumulative_cases'])
map_masterdf['Cumulative_deaths'] = np.log(map_masterdf['Cumulative_deaths'])

# print(map_masterdf)
mapfig = px.choropleth(map_masterdf,
                    locations='iso_code',
                    color="total_vaccinations",
                    color_continuous_scale="Reds",
                    hover_name='country',
                    hover_data={
                        'Cumulative_cases': True,
                        'Cumulative_deaths': True,
                        'total_vaccinations': True
                    },
                    title='Vaccination, cases, deaths Maps')
mapfig.update_layout(height=600)
mapfig.show()

## Vaccine over cases

In [37]:
print(vaccinedf_export.head())

    location             vaccine  total_vaccinations  Cumulative_cases  \
0  Argentina             CanSino              610540          10117518   
1  Argentina             Moderna             6507561          10117518   
2  Argentina  Oxford/AstraZeneca            25977231          10117518   
3  Argentina     Pfizer/BioNTech            14681054          10117518   
4  Argentina   Sinopharm/Beijing            28322602          10117518   

   Cumulative_deaths  id  
0             130820   0  
1             130820   1  
2             130820   2  
3             130820   3  
4             130820   4  


In [38]:
import plotly.express as px
bar_fig = px.bar(vaccinedf_export, x='location', y='total_vaccinations',
             color='vaccine', barmode='group',
             height=600)
bar_fig.show()

In [39]:

vacinne_fig = make_subplots(specs=[[{"secondary_y": True}]],
                   subplot_titles=['Cases and Deaths Count'])

# Bars on primary Y (vaccinations)
pivot_df = vaccinedf_export.pivot(index='location', columns='vaccine', values='total_vaccinations').fillna(0)
for region in pivot_df.columns:
    vacinne_fig.add_trace(go.Bar(
        x=pivot_df.index,
        y=pivot_df[region],
        name=region

    ))

# Line 1 on secondary Y (right)
vacinne_fig.add_trace(go.Scatter(x=vaccinedf_export['location'], y=vaccinedf_export['Cumulative_cases'],
                        mode='lines+markers', name='Cumulative Case',
                        line=dict(color='red', width=3)),
             secondary_y=True)

# Line 2 on secondary Y (right)
vacinne_fig.add_trace(go.Scatter(x=vaccinedf_export['location'], y=vaccinedf_export['Cumulative_deaths'],
                        mode='lines+markers', name='Cumulative Deaths',
                        line=dict(color='orange', width=3)),
             secondary_y=True)

# Dual-axis layout
vacinne_fig.update_layout(height=600, title='Vaccines, Death, Cases Dashboards')
vacinne_fig.update_xaxes(title_text='Country')
vacinne_fig.update_yaxes(title_text='Total Vaccination', secondary_y=False)
vacinne_fig.update_yaxes(title_text='Count', secondary_y=True)
vacinne_fig.show()